In [31]:
%load_ext autoreload
%autoreload 2
%matplotlib inline  

import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import plotly.offline as pl
pl.init_notebook_mode(connected=True)
import plotly.graph_objs as go

from datetime import datetime, timedelta
import parseIntervalFiles as pif
import parseActivityFiles as paf
#pun intended :)
import consolidateFiles as cf
import datacleaning as cl
import dataviz as dv

The autoreload extension is already loaded. To reload it, use:
  %reload_ext autoreload


In [32]:
verbose = True

PATH = "C:\\Users\\ju\\GDrive\\Projects\\HeRV\\Data\\"
RAW = PATH + "Raw"

In [33]:
file = PATH + "PreProcessed\\sessions.xlsx"
df = pd.read_excel(file)
df.sample(5)

activity  beatscount  duration            hf       hfnu  \
159             sleep        6637      5807  14415.879665  61.643020   
422          movement         612       478   3484.615691  64.259189   
41           movement        2750      1794    576.198635  43.650022   
72   household-chores        2696      1842   1138.325478  41.297767   
357  household-chores        1579       900     95.811330  11.794218   

              lf     lf_hf       lfnu         mhr        mrri   ...     \
159  8970.189956  0.622244  38.356980   73.333084  881.990508   ...      
422  1938.135116  0.556198  35.740811   78.781255  794.331699   ...      
41    743.843388  1.290950  56.349978  105.099822  585.364727   ...      
72   1618.059546  1.421438  58.702233   88.672785  689.798591   ...      
357   716.547172  7.478731  88.205782  103.507821  583.281824   ...      

      posture removed_artifacts       rmssd        sdnn               start  \
159       lie               155  203.458384  209.132784 2017-11-24 09:28:33   
422     stand                 7  123.950567  128.339730 2017-12-27 12:32:48   
41   standing                 1   38.225028   89.462412 2017-10-10 20:50:06   
72   standing                 9   72.370260   88.321641 2017-10-14 12:42:22   
357     stand                 0   17.738221   48.464415 2017-10-17 20:22:00   

                   stop   total_power user          vlf  sess_id  
159 2017-11-24 11:05:20  28288.892625    0  4902.823004      159  
422 2017-12-27 12:40:46   6212.589689    5   789.838882      422  
41  2017-10-10 21:20:00   1961.034600    0   640.992577       41  
72  2017-10-14 13:13:04   3865.289163    0  1108.904139       72  
357 2017-10-17 20:37:00   1320.490488    2   508.131987      357  

[5 rows x 23 columns]

In [34]:
len(df)

449

## Plotting random examples of RR time series for each type of activity

In [35]:
for act in df['activity'].unique():
    v = df[df['activity'] == act].sample(1)
    print('---------------- ', act, ' ---------------')
    for i in range(1):
        print('USER: ', v.iloc[i]['user'])
        dv.plot_sess_rr(v.iloc[i], RAW, act)

----------------  focused-active  ---------------
USER:  0


----------------  leisure  ---------------
USER:  0


----------------  eat  ---------------
USER:  5


----------------  movement  ---------------
USER:  0


----------------  sleep  ---------------
USER:  2


----------------  rest-passive  ---------------
USER:  0


----------------  rest-active  ---------------
USER:  5


----------------  household-chores  ---------------
USER:  0


----------------  focused-passive  ---------------
USER:  0


----------------  exercise  ---------------
USER:  3


### Removing outliers from frequency domain

In [36]:
dfc = df[df['hf'] < 7000]
print(len(df) - len(dfc))
print(len(dfc))

41
408


In [37]:
dfc = dfc[dfc['lf'] < 7000]
print(len(dfc))

407


## Plotting features summary for each type of session
---

In [38]:
for user in range(3):    
    dfu = dfc[dfc['user'] == user]
    print('---------------------------------------- ', user, ' ----------------------------------------')
    for feat in cl.features_all:
        dv.boxplot_compare(dfu, feat, groupby='activity', min_examples=2)

----------------------------------------  0  ----------------------------------------


----------------------------------------  1  ----------------------------------------


----------------------------------------  2  ----------------------------------------


## Assessing how features evolve within a session
---

### Load sessions fragmented in 60 seconds

In [39]:
fdf = pd.read_excel('../data/fragments/df_60_30.xlsx')

In [40]:
fdf.describe()

beatcount            hf          hfnu            lf         lf_hf  \
count  19233.000000  19233.000000  19233.000000  19233.000000  19233.000000   
mean      80.363334   1773.941653     49.715246   1531.153352      2.214625   
std       20.802385   2950.548394     25.388744   2840.047921      3.537051   
min       37.000000      0.077152      0.749662      0.173046      0.005172   
25%       68.000000    225.169651     27.548188    217.729426      0.399618   
50%       77.000000    580.018943     49.822851    596.142299      1.007111   
75%       87.000000   1604.705984     71.448061   1579.597222      2.630003   
max      186.000000  14976.717492     99.485487  38797.808704    132.393456   

               lfnu           mhr          mrri          nn50         order  \
count  19233.000000  19233.000000  19233.000000  19233.000000  19233.000000   
mean      50.284754     80.330579    793.353147     15.412052     90.554724   
std       25.388744     19.158152    168.537135     13.509879    113.640431   
min        0.514513     43.512674    327.907104      0.000000      0.000000   
25%       28.551939     68.751270    694.717647      4.000000     12.000000   
50%       50.177149     77.087860    785.960526     12.000000     36.000000   
75%       72.451812     87.477389    882.623188     24.000000    132.000000   
max       99.250338    183.052548   1382.954545    100.000000    571.000000   

              pnn50         rmssd          sdnn          sess   total_power  \
count  19233.000000  19233.000000  19233.000000  19233.000000  19233.000000   
mean      22.114158     61.525357     70.406003    213.207768   4763.583921   
std       20.560198     52.131322     45.708567    137.217487   6895.635161   
min        0.000000      1.424952      2.100095      0.000000      0.980344   
25%        4.878049     26.782073     38.349954     97.000000    962.270918   
50%       16.438356     42.529168     56.484266    188.000000   2101.509697   
75%       34.375000     79.151921     89.612703    349.000000   5157.723253   
max       94.444444    431.483256    328.385002    446.000000  70185.639553   

               user           vlf  
count  19233.000000  19233.000000  
mean       1.298393   1458.488916  
std        1.902666   3183.156723  
min        0.000000      0.000000  
25%        0.000000    180.706275  
50%        0.000000    514.230086  
75%        2.000000   1428.327446  
max        6.000000  61682.589010

### Helper to choose an activity

In [41]:
df.loc[(df['activity']=='movement') & (df['user']== 1)][['user', 'activity', 'start', 'duration', 'beatscount']].sort_values(by='duration', ascending=False)

user  activity               start  duration  beatscount
238     1  movement 2017-11-02 19:49:37      2178        3614
235     1  movement 2017-11-01 17:02:13      2072        3733
255     1  movement 2017-11-30 15:02:00       942         880
257     1  movement 2017-11-30 15:50:40       679         994

### Exercise
20 min switch exercise type (aerobic -> strength)

In [42]:
pp = fdf.loc[fdf['sess'] == 207].sort_values(by=['order'], ascending=True)
pl.iplot(dv.trace_sess_fragments(pp,['rmssd', 'mhr', 'sdnn', 'pnn50'], filter=3))

### Movement

In [43]:
pp = fdf.loc[fdf['sess'] == 198].sort_values(by=['order'], ascending=True)
pl.iplot(dv.trace_sess_fragments(pp,['rmssd', 'mhr', 'sdnn', 'pnn50'], filter=3))

### Sleeping

In [44]:
pp = fdf.loc[fdf['sess'] == 188].sort_values(by=['order'], ascending=True)
pl.iplot(dv.trace_sess_fragments(pp,['rmssd', 'mhr', 'sdnn', 'pnn50'], filter=5))

### A long session of lectures

In [45]:
pp = fdf.loc[fdf['sess'] == 31].sort_values(by=['order'], ascending=True)
pl.iplot(dv.trace_sess_fragments(pp,['rmssd', 'mhr', 'sdnn', 'pnn50'], filter=3))

### A single lecture
148 - lose focus after an hour <br>
107 - keep focus

In [46]:
pp = fdf.loc[fdf['sess'] == 107].sort_values(by=['order'], ascending=True)
pl.iplot(dv.trace_sess_fragments(pp,['rmssd', 'mhr', 'sdnn', 'pnn50'], filter=3))

### Work session
seems like a pomodoro break there :)

In [47]:
pp = fdf.loc[fdf['sess'] == 230].sort_values(by=['order'], ascending=True)
pl.iplot(dv.trace_sess_fragments(pp,['rmssd', 'mhr', 'sdnn', 'pnn50'], filter=3))

In [48]:
df.describe()

beatscount      duration            hf        hfnu            lf  \
count    449.000000    449.000000    449.000000  449.000000    449.000000   
mean    3956.723831   3151.884187   2180.088540   41.939632   1736.148680   
std     6532.976260   5762.267147   4391.992246   17.161628   1910.433850   
min      105.000000     88.000000     13.635122    8.241489     36.995074   
25%     1108.000000    900.000000    370.564885   28.873241    674.029791   
50%     1779.000000   1430.000000    721.050594   39.793389   1218.595371   
75%     3789.000000   2460.000000   1639.893215   55.015320   1976.091865   
max    46856.000000  34360.000000  49458.460876   85.318495  20551.688970   

            lf_hf        lfnu         mhr         mrri          nn50  \
count  449.000000  449.000000  449.000000   449.000000    449.000000   
mean     1.939087   58.060368   87.244239   731.137163    954.351893   
std      1.599788   17.161628   18.976790   142.258513   2664.966602   
min      0.172079   14.681505   54.190501   369.893825      0.000000   
25%      0.817676   44.984680   74.672025   641.662587     85.000000   
50%      1.512980   60.206611   83.213058   733.406699    243.000000   
75%      2.463415   71.126759   95.145346   817.112689    532.000000   
max     11.133730   91.758511  164.397688  1144.581425  20895.000000   

            pnn50  removed_artifacts       rmssd        sdnn   total_power  \
count  449.000000         449.000000  449.000000  449.000000    449.000000   
mean    17.545222          34.641425   65.835872   91.594234   5302.848776   
std     15.576111         228.402474   52.834681   44.369566   6978.924860   
min      0.000000           0.000000    5.402758   21.083352    150.076646   
25%      5.971151           0.000000   32.724557   62.458526   1752.397329   
50%     13.684211           1.000000   48.366812   78.552601   3207.787111   
75%     25.096031          14.000000   77.690378  108.602310   5278.123295   
max     81.780538        4670.000000  365.184163  269.251749  74465.121914   

             user          vlf     sess_id  
count  449.000000   449.000000  449.000000  
mean     1.269488  1386.611556  224.000000  
std      1.578590  1248.666812  129.759393  
min      0.000000    98.372239    0.000000  
25%      0.000000   575.914227  112.000000  
50%      1.000000  1028.660179  224.000000  
75%      2.000000  1718.395697  336.000000  
max      6.000000  7350.357547  448.000000

In [49]:
df.loc[df['activity'] == 'leisure-active']

Empty DataFrame
Columns: [activity, beatscount, duration, hf, hfnu, lf, lf_hf, lfnu, mhr, mrri, nn50, notes, pnn50, posture, removed_artifacts, rmssd, sdnn, start, stop, total_power, user, vlf, sess_id]
Index: []

[0 rows x 23 columns]

In [50]:
pp = fdf.loc[fdf['sess'] == 440].sort_values(by=['order'], ascending=True)
pl.iplot(dv.trace_sess_fragments(pp,['rmssd', 'mhr', 'sdnn', 'pnn50'], filter=3))